**Libraries & Data**

In [2]:
# load libraries
import pandas as pd
import plotly.figure_factory as FF
import plotly.express as px
import plotly.offline as pyo
import time

# set notebook mode to work in offline
pyo.init_notebook_mode(connected=True)

**Chart #1** : Bubble-Plot - Top 10 Artists Across KEXP History

In [ ]:
# load data
df = pd.read_csv("dataset_assets/kexp_sample.csv")
df = df[df["Artist"] != "(Various Artists) "]

/var/folders/q1/w97yxq494d39kypddsl0x40c0000gn/T/ipykernel_59395/3644743577.py:3: DtypeWarning:

Columns (11,12) have mixed types. Specify dtype option on import or set low_memory=False.



In [4]:
# review data

print(df.columns.tolist())  # list of columns

['DateTime', 'Program Name', 'Host', 'Song', 'Artist', 'Album', 'Labels', 'Release Date', 'Local?', 'Live?', 'Request?', 'Rotation Status', 'Comment']


In [5]:
# shape of the data

df.shape

(202928, 13)

In [6]:
# calculating top artists
artist_count = df['Artist'].value_counts().reset_index() # converting plays to a dataframe
artist_count.columns = ['Artist', 'Plays'] # renaming columns
artist_count = artist_count[artist_count['Artist'] != '(Various Artists) '] # removing '(Various Artists)' from the list
artist_count = artist_count.sort_values(by='Plays', ascending=False) # sorting the dataframe by plays
top_artists = artist_count.head(10) # selecting the top 10 artists
top_artists

# creating a formatted table for the top artists
table = FF.create_table(top_artists)
pyo.iplot(table)

In [7]:
# visulaization prepation

# create the animated table for top artists across time
df['DateTime'] = pd.to_datetime(df['DateTime'], errors='coerce', utc=True)      # converting DateTime to datetime format
df.dropna(subset=['DateTime'], inplace=True)        # dropping rows with missing DateTime values
df['DateTime'] = df['DateTime'].dt.tz_localize(None) # removing timezone information from DateTime column (error reduction)
df = df[df['Artist'] != '(Various Artists) ']     # removing '(Various Artists)' from the list 
df['Month'] = df['DateTime'].dt.to_period('M')      # extracting month from DateTime column

# aggregate play count per month and artist
artist_play_count = df.groupby(['Month', 'Artist']).size().reset_index(name='Plays')

# ensure all conbinations of months and artists are present in the data
all_months = pd.date_range(start=df['DateTime'].min(), end=df['DateTime'].max(), freq='M').to_period('M')       # create a list of all months
all_artists = artist_play_count['Artist'].unique()      # create a list of all artists
all_combinations = pd.MultiIndex.from_product([all_months, all_artists], names=['Month', 'Artist'])      # create a multi-index of all combinations
artist_play_count = artist_play_count.set_index(['Month', 'Artist']).reindex(all_combinations, fill_value=0).reset_index()      # reindex the data to include all combinations

# sort by month and compute cumulative plays per artist
artist_play_count = artist_play_count.sort_values(by='Month')
artist_play_count['TotalPlaysToDate'] = artist_play_count.groupby('Artist')['Plays'].expanding().sum().reset_index(level=0, drop=True)

top10_per_month = pd.DataFrame()        # create an empty dataframe to store the top 10 artists per month
for month in sorted(artist_play_count['Month'].unique()):       # iterate over each month
    cumulative_data = artist_play_count[artist_play_count['Month'] <= month]        # filter data for the month and all previous months
    cumulative_totals = cumulative_data.groupby('Artist')['TotalPlaysToDate'].max().reset_index()       # calculate the total plays per artist
    cumulative_totals['Month'] = month     # add the month to the dataframe
    top10_this_month = cumulative_totals.sort_values(by='TotalPlaysToDate', ascending=False).head(10)       # select the top 10 artists
    top10_this_month['Rank'] = range(1, len(top10_this_month) + 1)       # add the rank to the dataframe
    top10_per_month = pd.concat([top10_per_month, top10_this_month], ignore_index=True)     # append the data to the dataframe
    
# bubble size and cumulative plays
top10_per_month['PlaySize'] = top10_per_month['TotalPlaysToDate']

/var/folders/q1/w97yxq494d39kypddsl0x40c0000gn/T/ipykernel_59395/1540994462.py:14: FutureWarning:

'M' is deprecated and will be removed in a future version, please use 'ME' instead.



In [ ]:
# create visulaization

fig = px.scatter(
    top10_per_month,
    x='Rank',
    y='TotalPlaysToDate',
    size='PlaySize',
    color='Artist',
    animation_frame='Month',
    animation_group='Artist',
    text='Artist',
    #title="Who Dominated the KEXP Airwaves? Top 10 Artists Over Time",
    labels={'TotalPlaysToDate': 'Cumulative Plays by Artist', 'Rank': 'Rank'},
    height=1000,
    width=1400,
    size_max=65,
    color_discrete_sequence=px.colors.qualitative.Bold
)

fig.update_layout(
    title={
        'text': "Who Dominated the KEXP Airwaves? Top 10 Artists Over Time",
        'x': 0.5,  
        'xanchor': 'center',
        'yanchor': 'top'
    }, 
    showlegend=False,
    yaxis=dict(range=[0, top10_per_month['TotalPlaysToDate'].max() + 100]),
    xaxis=dict(
        tickmode='linear',
        dtick=1,
        range=[0.5, 10.5]
    )
)

fig.show()

In [46]:
fig.write_html("draft_kexp_1.html")

**Chart #2** : Stacked Bar Chart - Hosts Introduction of Unique Artists

In [ ]:
# load data
df = pd.read_csv("dataset_assets/kexp_sample.csv")

/var/folders/q1/w97yxq494d39kypddsl0x40c0000gn/T/ipykernel_66308/3644743577.py:3: DtypeWarning:

Columns (11,12) have mixed types. Specify dtype option on import or set low_memory=False.



In [5]:
df.shape

(202928, 13)

In [6]:
# data preparation for stacked bar chart

# normalize artist info
df['Artist'] = df['Artist'].str.strip().str.lower()  

# filter out hosts with commas, except 'Larry Mizell, Jr.'
df = df[~df['Host'].str.contains(',', na=False) | (df['Host'] == 'Larry Mizell, Jr.')]

# convert datetime to fit format and year & extract year from DateTime column
df['DateTime'] = pd.to_datetime(df['DateTime'], errors='coerce', utc=True)
df['Year'] = df['DateTime'].dt.year     

# ensure unique artist plays per year and host
unique_artist_host = df[['Artist', 'Host']].drop_duplicates()   # select unique artist plays per year and host 

# group by year, host, and artist
artist_counts = unique_artist_host.groupby('Host')['Artist'].nunique().reset_index()
artist_counts.rename(columns={'Artist': 'New Artists'}, inplace=True)

# find top 10 hosts with most new artists
top_hosts = artist_counts.nlargest(10, 'New Artists')['Host']

# filter data to only include top 10
filtered_df = df[df['Host'].isin(top_hosts)]
filtered_df = unique_artist_host[unique_artist_host['Host'].isin(top_hosts)]
filtered_df = df[['Year', 'Artist', 'Host']].drop_duplicates()      # only unqiue host/artist combinations - prevents carrying across years
filtered_df = filtered_df[filtered_df['Host'].isin(top_hosts)]      # only top 10 hosts

yearly_counts = filtered_df.groupby(['Year', 'Host'])['Artist'].nunique().reset_index()
yearly_counts.rename(columns={'Artist': 'New Artists'}, inplace=True)


In [7]:
# create table for hosts responsible for the most unique artists

# get top 10 hosts
top_hosts_df = artist_counts.groupby('Host')['New Artists'].sum().nlargest(10).reset_index()

# convert dataframe to a 2d list for table creation
table_data = [['Host', 'New Artists']] + top_hosts_df.values.tolist() 

# create and visualize table
table = FF.create_table(table_data)
pyo.iplot(table)

In [9]:
# create visualization for stacked bar chart

# plot data
fig2 = px.bar(
    yearly_counts,
    x='Year',
    y='New Artists',
    color='Host',
    title="KEXP Top 10 Hosts: Champions of New Artist Introductions",
    labels={'New Artists': 'Number of New Artists'},
    color_discrete_sequence=px.colors.sequential.Viridis
)

fig2.update_layout(
    title={
        'text': "KEXP Top 10 Hosts: Champions of New Artist Introductions",
        'x': 0.5,  
        'xanchor': 'center',
        'yanchor': 'top'
    }, 
    xaxis=dict(rangeslider=dict(visible=True), type='linear'),
    legend=dict(title='Host'),
    xaxis_title='Year',
    yaxis_title='Number of New Artists'
)

fig2.show()

In [51]:
fig2.write_html("draft_kexp_2.html")